In [7]:
import xml.etree.ElementTree as ET

def read_content(xml_file: str):

    tree = ET.parse(xml_file)
    root = tree.getroot()

    list_with_all_boxes = []

    for boxes in root.iter('object'):

        filename = root.find('filename').text

        ymin, xmin, ymax, xmax = None, None, None, None

        ymin = int(boxes.find("bndbox/ymin").text)
        xmin = int(boxes.find("bndbox/xmin").text)
        ymax = int(boxes.find("bndbox/ymax").text)
        xmax = int(boxes.find("bndbox/xmax").text)

        list_with_single_boxes = [xmin, ymin, xmax, ymax]
        list_with_all_boxes.append(list_with_single_boxes)

    return filename, list_with_all_boxes

In [8]:
import cv2
import os


#folder_Bboxes="ILSVRC2012_bbox_val_v3"
folder_Bboxes="ILSVRC2012_bbox_val_v3_All"

bbox_FileNames = []
for filename in os.listdir(folder_Bboxes):
    bbox_FileNames.append(filename)
bbox_FileNames.sort()  

In [9]:
import cv2
import os


folder_Images="ImagentDataset"

# last_fileName=""
imagesFileNames = []
for filename in os.listdir(folder_Images):
    imagesFileNames.append(filename)
imagesFileNames.sort()  

In [10]:
import cv2
import os


Hmpfolder_Images="HeatMaps_Folder"

HmpFileNames = []
for filename in os.listdir(Hmpfolder_Images):
    HmpFileNames.append(filename)
HmpFileNames.sort()

In [11]:
from collections import namedtuple
import numpy as np
import cv2
# define the `Detection` object
Detection = namedtuple("Detection", ["image_path", "gt", "pred"])

def bb_intersection_over_union(boxA, boxB):
	# determine the (x, y)-coordinates of the intersection rectangle
	xA = max(boxA[0], boxB[0])
	yA = max(boxA[1], boxB[1])
	xB = min(boxA[2], boxB[2])
	yB = min(boxA[3], boxB[3])
	# compute the area of intersection rectangle
	interArea = max(0, xB - xA + 1) * max(0, yB - yA + 1)
	# compute the area of both the prediction and ground-truth
	# rectangles
	boxAArea = (boxA[2] - boxA[0] + 1) * (boxA[3] - boxA[1] + 1)
	boxBArea = (boxB[2] - boxB[0] + 1) * (boxB[3] - boxB[1] + 1)
	# compute the intersection over union by taking the intersection
	# area and dividing it by the sum of prediction + ground-truth
	# areas - the interesection area
	iou = interArea / float(boxAArea + boxBArea - interArea)
	# return the intersection over union value
	return iou

In [12]:
def im2double(im):
	return cv2.normalize(im.astype('float'), None, 0.0, 1.0, cv2.NORM_MINMAX)

In [13]:
import cv2

def get_Box_From_heatMap(heatMapPath):

    image = cv2.imread(heatMapPath)
    gray = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)
    thresh = cv2.threshold(gray, 0, 255, cv2.THRESH_BINARY + cv2.THRESH_OTSU)[1]

    # Find contours
    cnts = cv2.findContours(thresh, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    ######### This instruction returns all the cnts (features or contours(visible pixels))

    cnts = cnts[0] if len(cnts) == 2 else cnts[1]
    c= max(cnts, key=cv2.contourArea)
    x,y,w,h = cv2.boundingRect(c)
    cv2.rectangle(image, (x, y), (x + w, y + h), (0,255,0), 3) ### original

    heatM_boxes = [x,y,w,h]

    cv2.waitKey()
    bbox_file1 = heatMapPath.replace('HeatMaps_Folder/','BBoxFiles_Result/')
    bbox_file = bbox_file1.replace('.JPEG','.txt')
#     print('bbox_file: ', bbox_file)
    f = open(bbox_file, "w")
    for i in range(2):
        f.write(str(x)+ " ")
        f.write(str(y)+ " ")
        f.write(str(w)+ " ")
        f.write(str(h)+ " ")
    f.close()

In [14]:
def compute_IoU_SuperImposed (imageFileName, original_box, htmap_box):
#     print('image path:', imageFileName)
    detection = Detection(imageFileName, original_box, htmap_box)
    # detection = Detection("Val_HetMaps/hummingbird_heatM.jpeg", boxes[0], heatM_boxes)

    image = cv2.imread(detection.image_path)
    #     det = Detection("bboxgenerator/sample_6.jpg.jpg", boxData_formulate, heat_map_rect)
    cv2.rectangle(image, tuple(detection.gt[:2]), 
        tuple(detection.gt[2:]), (0, 255, 0), 2)
    cv2.rectangle(image, tuple(detection.pred[:2]), 
        tuple(detection.pred[2:]), (0, 0, 255), 2)
    iou = bb_intersection_over_union(detection.gt,detection.pred )
    cv2.putText(image, "IoU: {:.4f}".format(iou), (10, 30),
        cv2.FONT_HERSHEY_SIMPLEX, 0.6, (0, 255, 0), 2)
#     print("{}: {:.4f}".format(detection.image_path, iou))

    # imag = im2double(image)*0.2

#     cv2.imshow("Show", image)
    cv2.waitKey(0)

#     import matplotlib.image as mpimg
#     import matplotlib.pyplot as plt

# #     ### Added for saving heatmap
# #     nameextracted = imageFileName.replace('ResultsIoU_SuperImpsed/','ResultsIoU/')  
# #     output_heatM = nameextracted.replace('JPEG','')  
#     output_heatM = imageFileName.replace('ImagentDataset','ResultsIoU_SuperImpsed/') 
# #     output_heatM = 'ResulstIoU_SuperImpsed/' + imageFileName
#     cv2.imwrite(output_heatM, image)
    #img_hM=mpimg.imread(output_heatM)
    #plt.imshow(img_hM)
    #return iou

In [15]:
def compute_IoU (imageFileName, original_box, htmap_box):
    detection = Detection(imageFileName, original_box, htmap_box)

    # detection = Detection("Val_HetMaps/hummingbird_heatM.jpeg", boxes[0], heatM_boxes)
#     print('image IoU path', detection.image_path)
    image = cv2.imread(detection.image_path)
    #     det = Detection("bboxgenerator/sample_6.jpg.jpg", boxData_formulate, heat_map_rect)
    cv2.rectangle(image, tuple(detection.gt[:2]), 
        tuple(detection.gt[2:]), (0, 255, 0), 2)
    cv2.rectangle(image, tuple(detection.pred[:2]), 
        tuple(detection.pred[2:]), (0, 0, 255), 2)
    iou = bb_intersection_over_union(detection.gt,detection.pred )
    cv2.putText(image, "IoU: {:.4f}".format(iou), (10, 30),
        cv2.FONT_HERSHEY_SIMPLEX, 0.6, (0, 255, 0), 2)
#     print("{}: {:.4f}".format(detection.image_path, iou))

    # imag = im2double(image)*0.2

#     cv2.imshow("Show", image)
    cv2.waitKey(0)

    import matplotlib.image as mpimg
    import matplotlib.pyplot as plt

    ### Added for saving heatmap
    ### Added for saving heatmap
#     output_heatM = imageFileName.replace('HeatMaps_Folder/','ResultsIoU/')  
#     print('output hmp name: ', output_heatM)
#     cv2.imwrite(output_heatM, image)
#     img_hM=mpimg.imread(output_heatM)
#     plt.imshow(img_hM)
    return iou

# Final accuracy results reported in the paper are found at the end of final output cel

In [16]:
import os
import numpy as np
import cv2
from py_map2jpg import py_map2jpg

imageCount = 0
IoUCorrect = 0
htmpCounted =0

for image in HmpFileNames: ## modied as some heamaps not generated yet    
#     name, boxes = read_content("ILSVRC2012_bbox_val_v3_IoU"+ "/" + bbox_FileNames[imageCount])
    boxName = image.replace('.JPEG','.xml')
    name, boxes = read_content("ILSVRC2012_bbox_val_v3_All"+ "/" + boxName)
    if len(boxes)==1: ### ommit images with multiple objects
        box = boxes[0]
        Detection = namedtuple("Detection", ["image_path", "gt", "pred"])
        
        
        bbox_threshold = [20, 100, 110] # parameters for the bbox generator
        curParaThreshold = str(bbox_threshold[0])+' '+str(bbox_threshold[1])+' '+str(bbox_threshold[2])+' '
        curHeatMapFile = Hmpfolder_Images+ '/' + HmpFileNames[imageCount];
        curImgFile = folder_Images+ '/' + image;      
        #print('hmp name', curHeatMapFile)
        get_Box_From_heatMap(curHeatMapFile)#### get the bbox from heatmap
    #     imageName = imagesFileNames[imageCount]### original
        imageName = HmpFileNames[imageCount] ## modified to depend on HeatMaps_Folder/atmap data not images

       # print('image name:', imageName)
        curBBoxFile = ""
        bboxFileName =""
        if '.JPEG' in imageName:
            #print('bbox name', bboxFileName)
            bboxFileName = imageName.replace('.JPEG','')
            curBBoxFile = 'BBoxFiles_Result' + '/' + bboxFileName + '.txt';

        # os.system("bboxgenerator/./dt_box "+curHeatMapFile+' '+curParaThreshold+' '+curBBoxFile)


        with open(curBBoxFile) as f:
            for line in f:
                items = [int(x) for x in line.strip().split()]
        boxData1 = np.array(items[0::4]).T
        boxData2 = np.array(items[1::4]).T
        boxData3 = np.array(items[2::4]).T
        boxData4 = np.array(items[3::4]).T

        #print(boxData1)


        boxData_formulate = np.array([boxData1, boxData2, boxData1+boxData3, boxData2+boxData4]).T

        col1 = np.min(np.array([boxData_formulate[:,0], boxData_formulate[:,2]]), axis=0)
        col2 = np.min(np.array([boxData_formulate[:,1], boxData_formulate[:,3]]), axis=0)
        col3 = np.max(np.array([boxData_formulate[:,0], boxData_formulate[:,2]]), axis=0)
        col4 = np.max(np.array([boxData_formulate[:,1], boxData_formulate[:,3]]), axis=0)

        boxData_formulate = np.array([col1, col2, col3, col4]).T

        curHeatMap = cv2.imread(curHeatMapFile)
        curImg = cv2.imread(curImgFile)

        curHeatMap = im2double(curImg)*0.2+im2double(curHeatMap)*0.7
        origin_box = []
        htmap_box=[]
        for i in range(boxData_formulate.shape[0]): # for each bbox
            if i==0:
                origin_box= [boxData_formulate[i][0], boxData_formulate[i][1], boxData_formulate[i][2], boxData_formulate[i][3]]
                cv2.rectangle(curHeatMap, tuple(boxData_formulate[i][:2]), tuple(boxData_formulate[i][2:]), (0,255,0), 3)        
            else:
                htmap_box= [boxData_formulate[i][0], boxData_formulate[i][1], boxData_formulate[i][2], boxData_formulate[i][3]]
                print(boxData_formulate[i][:2])
                print(boxData_formulate[i][2:])
                cv2.rectangle(curHeatMap, tuple(boxData_formulate[i][:2]), tuple(boxData_formulate[i][2:]), (255,0,0), 3)

        IoU = compute_IoU(curHeatMapFile, box, htmap_box)
        compute_IoU_SuperImposed(curImgFile, box, htmap_box)
        #print ('IoU', IoU)
        if IoU>=0.5:
            IoUCorrect+=1
        print('total IoU correct', IoUCorrect)
        print('total hmp', htmpCounted)
        print(' WSOL accuracy:', IoUCorrect/(htmpCounted +1))
        print(' WSOL GT-known error:', 1 - (IoUCorrect/(htmpCounted +1)))
        htmpCounted +=1
    imageCount +=1
print('total hmp counted', htmpCounted)
print('total images counted', imageCount)
print('total correct', IoUCorrect)

[101  94]
[409 197]
total IoU correct 1
total hmp 0
 WSOL accuracy: 1.0
 WSOL GT-known error: 0.0
[142  33]
[407 270]
total IoU correct 1
total hmp 1
 WSOL accuracy: 0.5
 WSOL GT-known error: 0.5
[78  0]
[500 286]
total IoU correct 2
total hmp 2
 WSOL accuracy: 0.6666666666666666
 WSOL GT-known error: 0.33333333333333337
[0 0]
[500 333]
total IoU correct 3
total hmp 3
 WSOL accuracy: 0.75
 WSOL GT-known error: 0.25
[105 178]
[371 307]
total IoU correct 4
total hmp 4
 WSOL accuracy: 0.8
 WSOL GT-known error: 0.19999999999999996
[112  71]
[500 246]
total IoU correct 5
total hmp 5
 WSOL accuracy: 0.8333333333333334
 WSOL GT-known error: 0.16666666666666663
[ 43 117]
[277 382]
total IoU correct 5
total hmp 6
 WSOL accuracy: 0.7142857142857143
 WSOL GT-known error: 0.2857142857142857
[0 0]
[500 257]
total IoU correct 6
total hmp 7
 WSOL accuracy: 0.75
 WSOL GT-known error: 0.25
[150  34]
[500 400]
total IoU correct 7
total hmp 8
 WSOL accuracy: 0.7777777777777778
 WSOL GT-known error: 0.222

[ 93 102]
[351 237]
total IoU correct 54
total hmp 68
 WSOL accuracy: 0.782608695652174
 WSOL GT-known error: 0.21739130434782605
[ 0 65]
[377 334]
total IoU correct 55
total hmp 69
 WSOL accuracy: 0.7857142857142857
 WSOL GT-known error: 0.2142857142857143
[161  35]
[423 316]
total IoU correct 55
total hmp 70
 WSOL accuracy: 0.7746478873239436
 WSOL GT-known error: 0.22535211267605637
[ 0 35]
[253 380]
total IoU correct 56
total hmp 71
 WSOL accuracy: 0.7777777777777778
 WSOL GT-known error: 0.2222222222222222
[38 57]
[217 282]
total IoU correct 56
total hmp 72
 WSOL accuracy: 0.7671232876712328
 WSOL GT-known error: 0.23287671232876717
[74 55]
[412 331]
total IoU correct 56
total hmp 73
 WSOL accuracy: 0.7567567567567568
 WSOL GT-known error: 0.2432432432432432
[ 99 114]
[426 241]
total IoU correct 57
total hmp 74
 WSOL accuracy: 0.76
 WSOL GT-known error: 0.24
[76 96]
[341 363]
total IoU correct 58
total hmp 75
 WSOL accuracy: 0.7631578947368421
 WSOL GT-known error: 0.2368421052631

[ 0 38]
[714 414]
total IoU correct 97
total hmp 134
 WSOL accuracy: 0.7185185185185186
 WSOL GT-known error: 0.28148148148148144
[ 0 41]
[500 307]
total IoU correct 98
total hmp 135
 WSOL accuracy: 0.7205882352941176
 WSOL GT-known error: 0.27941176470588236
[80 51]
[500 314]
total IoU correct 99
total hmp 136
 WSOL accuracy: 0.7226277372262774
 WSOL GT-known error: 0.2773722627737226
[29 44]
[261 341]
total IoU correct 100
total hmp 137
 WSOL accuracy: 0.7246376811594203
 WSOL GT-known error: 0.2753623188405797
[ 82 106]
[419 272]
total IoU correct 101
total hmp 138
 WSOL accuracy: 0.7266187050359713
 WSOL GT-known error: 0.27338129496402874
[0 0]
[371 324]
total IoU correct 102
total hmp 139
 WSOL accuracy: 0.7285714285714285
 WSOL GT-known error: 0.27142857142857146
[130 129]
[500 375]
total IoU correct 102
total hmp 140
 WSOL accuracy: 0.723404255319149
 WSOL GT-known error: 0.276595744680851
[0 0]
[500 375]
total IoU correct 103
total hmp 141
 WSOL accuracy: 0.7253521126760564
 W

[94 64]
[362 395]
total IoU correct 145
total hmp 199
 WSOL accuracy: 0.725
 WSOL GT-known error: 0.275
[0 0]
[436 334]
total IoU correct 146
total hmp 200
 WSOL accuracy: 0.7263681592039801
 WSOL GT-known error: 0.2736318407960199
[214  67]
[355 382]
total IoU correct 147
total hmp 201
 WSOL accuracy: 0.7277227722772277
 WSOL GT-known error: 0.2722772277227723
[41 86]
[329 500]
total IoU correct 147
total hmp 202
 WSOL accuracy: 0.7241379310344828
 WSOL GT-known error: 0.27586206896551724
[ 0 60]
[428 375]
total IoU correct 148
total hmp 203
 WSOL accuracy: 0.7254901960784313
 WSOL GT-known error: 0.27450980392156865
[0 0]
[500 340]
total IoU correct 149
total hmp 204
 WSOL accuracy: 0.7268292682926829
 WSOL GT-known error: 0.2731707317073171
[85 53]
[358 269]
total IoU correct 150
total hmp 205
 WSOL accuracy: 0.7281553398058253
 WSOL GT-known error: 0.27184466019417475
[ 0 26]
[500 375]
total IoU correct 151
total hmp 206
 WSOL accuracy: 0.7294685990338164
 WSOL GT-known error: 0.27

[ 0 45]
[225 375]
total IoU correct 192
total hmp 264
 WSOL accuracy: 0.7245283018867924
 WSOL GT-known error: 0.2754716981132076
[102  72]
[273 423]
total IoU correct 193
total hmp 265
 WSOL accuracy: 0.7255639097744361
 WSOL GT-known error: 0.2744360902255639
[93 62]
[436 436]
total IoU correct 194
total hmp 266
 WSOL accuracy: 0.7265917602996255
 WSOL GT-known error: 0.27340823970037453
[0 0]
[446 375]
total IoU correct 195
total hmp 267
 WSOL accuracy: 0.7276119402985075
 WSOL GT-known error: 0.2723880597014925
[154  26]
[685 385]
total IoU correct 196
total hmp 268
 WSOL accuracy: 0.7286245353159851
 WSOL GT-known error: 0.27137546468401486
[155   0]
[500 500]
total IoU correct 196
total hmp 269
 WSOL accuracy: 0.725925925925926
 WSOL GT-known error: 0.274074074074074
[197  14]
[397 224]
total IoU correct 197
total hmp 270
 WSOL accuracy: 0.7269372693726938
 WSOL GT-known error: 0.27306273062730624
[0 0]
[500 375]
total IoU correct 198
total hmp 271
 WSOL accuracy: 0.7279411764705

...

[446 419]
total IoU correct 25725
total hmp 38035
 WSOL accuracy: 0.676332947733726
 WSOL GT-known error: 0.323667052266274
[0 0]
[333 442]
total IoU correct 25725
total hmp 38036
 WSOL accuracy: 0.6763151668112627
 WSOL GT-known error: 0.3236848331887373
[74 89]
[293 330]
total IoU correct 25726
total hmp 38037
 WSOL accuracy: 0.6763236763236763
 WSOL GT-known error: 0.3236763236763237
[40 86]
[434 296]
total IoU correct 25727
total hmp 38038
 WSOL accuracy: 0.67633218538868
 WSOL GT-known error: 0.32366781461132
[0 0]
[252 427]
total IoU correct 25727
total hmp 38039
 WSOL accuracy: 0.6763144058885384
 WSOL GT-known error: 0.3236855941114616
[72 17]
[435 334]
total IoU correct 25728
total hmp 38040
 WSOL accuracy: 0.6763229147498752
 WSOL GT-known error: 0.32367708525012484
[57  0]
[330 422]
total IoU correct 25729
total hmp 38041
 WSOL accuracy: 0.6763314231638715
 WSOL GT-known error: 0.3236685768361285
[ 0 68]
[270 437]
total IoU correct 25729
total hmp 38042
 WSOL accuracy: 0.676

[533 371]
[1281 1087]
total IoU correct 25768
total hmp 38098
 WSOL accuracy: 0.6763432111079031
 WSOL GT-known error: 0.3236567888920969
[ 0 54]
[500 375]
total IoU correct 25768
total hmp 38099
 WSOL accuracy: 0.6763254593175853
 WSOL GT-known error: 0.32367454068241475
[ 0 63]
[442 330]
total IoU correct 25768
total hmp 38100
 WSOL accuracy: 0.6763077084590956
 WSOL GT-known error: 0.3236922915409044
[ 0 76]
[375 392]
total IoU correct 25769
total hmp 38101
 WSOL accuracy: 0.6763162038738124
 WSOL GT-known error: 0.3236837961261876
[68 26]
[337 278]
total IoU correct 25770
total hmp 38102
 WSOL accuracy: 0.6763246988426108
 WSOL GT-known error: 0.3236753011573892
[177  82]
[338 307]
total IoU correct 25771
total hmp 38103
 WSOL accuracy: 0.6763331933655259
 WSOL GT-known error: 0.3236668066344741
[73 69]
[338 367]
total IoU correct 25772
total hmp 38104
 WSOL accuracy: 0.6763416874425928
 WSOL GT-known error: 0.3236583125574072
[ 0 58]
[333 500]
total IoU correct 25772
total hmp 381

[210 112]
[441 333]
total IoU correct 25810
total hmp 38161
 WSOL accuracy: 0.6763272365180022
 WSOL GT-known error: 0.3236727634819978
[81 70]
[472 288]
total IoU correct 25811
total hmp 38162
 WSOL accuracy: 0.6763357178418887
 WSOL GT-known error: 0.32366428215811127
[98 31]
[285 436]
total IoU correct 25811
total hmp 38163
 WSOL accuracy: 0.676317996017189
 WSOL GT-known error: 0.323682003982811
[  0 132]
[500 375]
total IoU correct 25812
total hmp 38164
 WSOL accuracy: 0.6763264771387397
 WSOL GT-known error: 0.3236735228612603
[67 44]
[283 324]
total IoU correct 25813
total hmp 38165
 WSOL accuracy: 0.6763349578158571
 WSOL GT-known error: 0.32366504218414294
[ 65 166]
[500 500]
total IoU correct 25813
total hmp 38166
 WSOL accuracy: 0.6763172374040402
 WSOL GT-known error: 0.32368276259595985
[  0 188]
[479 500]
total IoU correct 25814
total hmp 38167
 WSOL accuracy: 0.6763257178788514
 WSOL GT-known error: 0.32367428212114857
[ 0 57]
[440 500]
total IoU correct 25814
total hmp 

[ 0 71]
[417 400]
total IoU correct 25852
total hmp 38222
 WSOL accuracy: 0.676346702247338
 WSOL GT-known error: 0.32365329775266205
[0 0]
[192 303]
total IoU correct 25853
total hmp 38223
 WSOL accuracy: 0.6763551695269987
 WSOL GT-known error: 0.3236448304730013
[26 60]
[434 375]
total IoU correct 25854
total hmp 38224
 WSOL accuracy: 0.6763636363636364
 WSOL GT-known error: 0.3236363636363636
[60  0]
[436 419]
total IoU correct 25855
total hmp 38225
 WSOL accuracy: 0.6763721027572857
 WSOL GT-known error: 0.32362789724271435
[48  0]
[375 427]
total IoU correct 25856
total hmp 38226
 WSOL accuracy: 0.6763805687079812
 WSOL GT-known error: 0.32361943129201876
[ 25 104]
[294 500]
total IoU correct 25857
total hmp 38227
 WSOL accuracy: 0.6763890342157581
 WSOL GT-known error: 0.32361096578424187
[81 58]
[345 408]
total IoU correct 25857
total hmp 38228
 WSOL accuracy: 0.6763713411284626
 WSOL GT-known error: 0.32362865887153736
[71  0]
[640 410]
total IoU correct 25858
total hmp 38229


[92 68]
[660 359]
total IoU correct 25901
total hmp 38283
 WSOL accuracy: 0.676548949952983
 WSOL GT-known error: 0.323451050047017
[ 0 59]
[500 324]
total IoU correct 25902
total hmp 38284
 WSOL accuracy: 0.6765573984589265
 WSOL GT-known error: 0.3234426015410735
total hmp counted 38285
total images counted 38285
